In [224]:
from validator.InstanceCO22 import InstanceCO22
import warnings
from collections import OrderedDict
warnings.filterwarnings( "ignore", module = "matplotlib\..*" )
from util import *
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import networkx as nx
from vrpy import VehicleRoutingProblem
import pprint
import warnings
import logging
import llist
import pandas as pd
from typing import List, Set, Tuple, Dict
import random
import time
import copy
from dataClasses import * 
from cachetools import cached
warnings.filterwarnings("ignore", module="vrpy\..*")


logger = logging.getLogger(__name__)
logging.basicConfig(level=logging.CRITICAL)
%reload_ext autoreload
%autoreload 2

## Initial solution

In [225]:
def distance(loc1: InstanceCO22.Location, loc2: InstanceCO22.Location, ceil: bool = True) -> float:
    dist = math.sqrt((loc1.X - loc2.X)**2 + (loc1.Y - loc2.Y)**2)
    if ceil:
        return math.ceil(dist)
    else:
        return dist


def requestClosestHub(instance: InstanceCO22, request: InstanceCO22.Request) -> int:
    nHubs = len(instance.Hubs)
    hubs = instance.Locations[1:nHubs+1]
    minDist = math.inf
    minDistHubLocID = None
    for i, hub in enumerate(hubs):
        if request.ID in instance.Hubs[i].allowedRequests:
            hubDist = distance(
                instance.Locations[request.customerLocID-1], hub)
            if hubDist < minDist:
                minDist = hubDist
                minDistHubLocID = hub.ID
    return minDistHubLocID


def requestsClosestHub(instance: InstanceCO22) -> dict:
    # return dictionary of {'LOC_ID': ' NEAREST LOC_ID'}
    res = {}
    for req in instance.Requests:
        res[req.ID] = requestClosestHub(instance, req)
    return res


def requestsPerHub(instance: InstanceCO22) -> dict:
    closestHubPerRequest = requestsClosestHub(instance=instance)
    nHubs = len(instance.Hubs)
    hubLocIDs = list(range(2, nHubs+2))
    res = {val: [] for val in hubLocIDs}
    for hubLocID in hubLocIDs:
        for reqID, closestHubLocID in closestHubPerRequest.items():
            if closestHubLocID is hubLocID:
                res[hubLocID].append(reqID)
    return res


def amountPerProduct(instance: InstanceCO22, requests: list) -> list:
    nProducts = len(instance.Products)
    res = [None]*nProducts
    for i in range(nProducts):
        res[i] = sum([req.amounts[i] for req in requests])
    return res


def filterRequests(instance: InstanceCO22, day: int = None, locationsID: int = None) -> list:
    res = instance.Requests.copy()
    if day != None:
        res = [_ for _ in res if _.desiredDay is day]
    if locationsID != None:
        res = [_ for _ in res if _.customerLocID in locationsID]
    return res


def addAllEdges(G: nx.DiGraph, checkWindowOverlap: bool = False) -> nx.DiGraph:
    for locID1, node1 in G.nodes(data=True):
        for locID2, node2 in G.nodes(data=True):
            if locID1 != locID2:
                if checkWindowOverlap and locID1 not in ["Source", "Sink"] and locID2 not in ["Source", "Sink"] and not windowOverlap(node1['periodIDs'], node2['periodIDs']):
                    continue
                dist = math.ceil(
                    math.sqrt(pow(node1['X']-node2['X'], 2) + pow(node1['Y']-node2['Y'], 2)))
                if locID1 == "Sink" or locID2 == "Source" or (locID1 == "Source" and locID2 == "Sink"):
                    continue
                else:
                    G.add_edge(locID1, locID2, time=dist, cost=dist)
    return G


def createNxHub(instance: InstanceCO22, hubLocID: int, requests: list) -> nx.DiGraph:
    G = nx.DiGraph()
    for req in requests:
        reqLoc = instance.Locations[req.customerLocID-1]
        G.add_node(req.ID, locID=reqLoc.ID, reqID=req.ID, X=reqLoc.X,
                   Y=reqLoc.Y, demand=sum(req.amounts), amounts=req.amounts)
    hubLoc = instance.Locations[hubLocID]
    G.add_node("Source", locID=hubLocID, X=hubLoc.X, Y=hubLoc.Y)
    G.add_node("Sink", locID=hubLocID, X=hubLoc.X, Y=hubLoc.Y)
    G = addAllEdges(G)
    return G


def solveHubVRP(instance: InstanceCO22, hubLocID: int, requests: list) -> dict:
    # create networkX
    G = createNxHub(instance, hubLocID, requests)
    G_dict = {i: v for i, v in G.nodes(data=True)}
    # print(G_dict.keys())
    prob = VehicleRoutingProblem(G, load_capacity=instance.VanCapacity)
    prob.duration = instance.VanMaxDistance
    prob.fixed_cost = instance.VanDayCost
    prob.solve()
    best_routes = prob.best_routes
    #best_routes = {id:listReplace(best_routes[id], ["Source","Sink"], hubLocID) for id in best_routes.keys()}
    res = {
        'routes': {key: {'route': [G_dict[id] for id in best_routes[key]]} for key in best_routes.keys()},
        'demand': sum([sum(req.amounts) for req in requests]),
        'amounts': amountPerProduct(instance, requests)
    }
    return res


def createNxDepot(instance: InstanceCO22, dayRoutes: dict) -> nx.DiGraph:
    G = nx.DiGraph()
    # add hubs
    for (day, hubLocID), hubData in dayRoutes.items():
        G.add_node(f"{hubLocID}.1", locID=hubLocID, demand=0, amounts=0,
                   X=instance.Locations[hubLocID-1].X, Y=instance.Locations[hubLocID-1].Y)

    for (day, hubLocID), hubData in dayRoutes.items():
        i = 1
        nodeID = f"{hubLocID}.{i}"
        while nodeID in G.nodes and G.nodes[nodeID]['demand'] + hubData['demand'] > instance.TruckCapacity:
            i += 1
            nodeID = f"{hubLocID}.{i}"
        if nodeID not in G.nodes:
            G.add_node(nodeID, locID=hubLocID, demand=0, amounts=0,
                       X=instance.Locations[hubLocID-1].X, Y=instance.Locations[hubLocID-1].Y)

        G.nodes[nodeID]['amounts'] = list(
            np.array(G.nodes[nodeID]['amounts']) + np.array(hubData['amounts']))
        G.nodes[nodeID]['demand'] = G.nodes[nodeID]['demand']+hubData['demand']

    G.add_node("Source", locID=1,
               X=instance.Locations[0].X, Y=instance.Locations[0].Y)
    G.add_node("Sink", locID=1,
               X=instance.Locations[0].X, Y=instance.Locations[0].Y)

    G = addAllEdges(G)
    return G


def solveDepotVRP(instance: InstanceCO22, dayRoutes: dict) -> dict:
    # for solving per day
    G = createNxDepot(instance, dayRoutes)
    G_dict = {i: v for i, v in G.nodes(data=True)}
    print(G_dict.keys())

    prob = VehicleRoutingProblem(G, load_capacity=instance.TruckCapacity)
    prob.duration = instance.TruckMaxDistance
    prob.fixed_cost = instance.TruckDayCost
    prob.solve()
    best_routes = prob.best_routes
    #print(best_routes)
    #best_routes = {id:listReplace(best_routes[id], ["Source","Sink"], hubLocID) for id in best_routes.keys()}
    res = {key: [G_dict[id] for id in best_routes[key]]
           for key in best_routes.keys()}
    #print(res)
    return res

@cached(
    cache={},
    key=lambda a: a.CACHE_ID
)
def solveHub(instance: InstanceCO22) -> dict:
    nDays = instance.Days
    nHubs = len(instance.Hubs)
    hubLocIDs = list(range(2,nHubs+2))
    hubClusters = requestsPerHub(instance)
    hubRoutes = {}  
    for day in range(1, nDays+1):                                                   #hub routing
        dayRoutes = {}
        for hubLocID in hubLocIDs:
            hubCluster = hubClusters[hubLocID]
            #requestsToServe = filterRequests(instance, day, hubCluster)
            requestsToServe =[_ for _ in instance.Requests if _.ID in hubCluster and _.desiredDay is day]
            #print(hubCluster, [_.ID for _ in requestsToServe])   #
            if(len(requestsToServe) > 0):
                dayHubRoutes = solveHubVRP(instance, hubLocID, requestsToServe)
                dayRoutes[hubLocID] = dayHubRoutes
        hubRoutes[day] = dayRoutes
    return hubRoutes

In [415]:
%%capture
instance = loadInstance(10)
res = solveHub(instance)

INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 1084 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1084 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1084.0
INFO:vrpy.master_solve_pulp:total cost = 1084.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 1032 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1032 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1032.0
INFO:vrpy.master_solve_pulp:total cost = 1032.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 1068 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1068 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1068.0
INFO:vrpy.master_solve_pulp:total cost = 1068.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 1085 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 10

In [418]:
dm = DistanceMatrix(instance)
sum([dm.byReqID(i,i+1) for i in range(1,len(instance.Requests))])

4667.0

In [62]:
#test route distance and demand calculation 

#add all requests in one route orderer by reqID
hubLocID = 2
nodes = [Node(_.ID, _.customerLocID, _.amounts, instance.Locations[_.customerLocID-1].X, instance.Locations[_.customerLocID-1].Y, isHub=False) for _ in instance.Requests]
route = HubRoute(routeID=1, hubLocID=hubLocID)
route.addNodes(nodes)
dm = DistanceMatrix(instance)

assert route.length(distanceMatrix = dm) == sum([dm.byReqID(i,i+1) for i in range(1,len(instance.Requests))]) + dm.byReqIDLocID(instance.Requests[0].ID,hubLocID) + dm.byReqIDLocID(instance.Requests[-1].ID,hubLocID)
assert route.demand() == sum([sum(_.amounts) for _ in instance.Requests])
assert route.demand() == sum(route.amounts())
#test route insertion  after id. 
node1= Node(1,1,[1,1,1],10,1)
node2= Node(2,1,[1,1,1],10,1)
node3= Node(3,1,[1,1,1],10,1)
node4= Node(4,1,[1,1,1],10,1)
route = HubRoute(1,1)
route.addNodes([node1, node2, node3]) 
route.insertNodeAfter(2, node4) # insert node4 after reqID 2
route
assert route.nodes[2].reqID == 4

node4= Node(5,1,[1,1,1],10,1)
route.replaceNode(1,node4)
assert route.nodes[0].reqID == 5

AttributeError: 'DistanceMatrix' object has no attribute 'instance'

In [226]:
def parseToDayHubroutes(res):
    i = 0
    hubRoutesObject = HubRoutes()
    #take dictionary with structure as hubRoutes datamodel
    for day, dayData in res.items():
        dayHubRoutesObject = DayHubRoutes()
        for hubLocID, hubData in dayData.items():
            for routeID, routeData in hubData['routes'].items():
                route = HubRoute(i, hubLocID)
                for node in routeData['route'][1:-1]: #ignore source and sink
                    nodeObject = Node(reqID = node['reqID'], locID=node['locID'], amounts=node['amounts'], X=node['X'], Y=node['Y'])
                    route.addNode(nodeObject)
                dayHubRoutesObject.addRoute(route)
        hubRoutesObject.addDayHubRoutes(day=day,dayHubRoutes=dayHubRoutesObject)
    return hubRoutesObject

In [91]:
#test DayHubRoutes distance and demand calculation 

#add all requests in one route orderer by reqID
nodes = [Node(_.ID, _.customerLocID, _.amounts, instance.Locations[_.customerLocID-1].X, instance.Locations[_.customerLocID-1].Y, isHub=False) for _ in instance.Requests]

route1 = HubRoute(routeID=1, hubLocID=1)
route1.addNodes(nodes[0:10])

route2 = HubRoute(routeID=2, hubLocID=2)
route2.addNodes(nodes[10:20])

dayHubRoutes = DayHubRoutes()
dayHubRoutes.addRoute(route1)
dayHubRoutes.addRoute(route2)
dayHubRoutes.addRoute(route2)
print(dayHubRoutes.hubsUsed())
print(dayHubRoutes.nHubs())
print(dayHubRoutes.isFeasible(instance.VanCapacity, instance.VanMaxDistance, dm, verbose=True))
print(dayHubRoutes.coversRequestIDs([1,2,3,4,5]))


#random merge
route1 = HubRoute(routeID=1, hubLocID=1)
route1.addNodes(nodes[0:3])

route2 = HubRoute(routeID=2, hubLocID=2)
route2.addNodes(nodes[3:6])

dayHubRoutes = DayHubRoutes()
dayHubRoutes.addRoute(route1)
dayHubRoutes.addRoute(route2)

print("-"*20)
print(dayHubRoutes)
print("-"*10)
dayHubRoutes.randomMergeRoutes()
print(dayHubRoutes)

#random section insertion
route1 = HubRoute(routeID=1, hubLocID=1)
route1.addNodes(nodes[0:5])

route2 = HubRoute(routeID=2, hubLocID=2)
route2.addNodes(nodes[5:10])

dayHubRoutes = DayHubRoutes()
dayHubRoutes.addRoute(route1)
dayHubRoutes.addRoute(route2)

print("-"*20)
print(dayHubRoutes)
print("-"*10)
dayHubRoutes.randomSectionInsertion()
print(dayHubRoutes)


{1, 2}
2
Route with id 1 has a demand of 52 > vanCapacity = 30
Route with id 2 has a demand of 58 > vanCapacity = 30
Route with id 2 has a demand of 58 > vanCapacity = 30
False
True
--------------------
HubRoute from hub 1: Node(reqID:1, locID:4) -> Node(reqID:2, locID:22) -> Node(reqID:3, locID:12)
HubRoute from hub 2: Node(reqID:4, locID:23) -> Node(reqID:5, locID:22) -> Node(reqID:6, locID:16)

----------
HubRoute from hub 2: Node(reqID:4, locID:23) -> Node(reqID:5, locID:22) -> Node(reqID:6, locID:16) -> Node(reqID:1, locID:4) -> Node(reqID:2, locID:22) -> Node(reqID:3, locID:12)

--------------------
HubRoute from hub 1: Node(reqID:1, locID:4) -> Node(reqID:2, locID:22) -> Node(reqID:3, locID:12) -> Node(reqID:4, locID:23) -> Node(reqID:5, locID:22)
HubRoute from hub 2: Node(reqID:6, locID:16) -> Node(reqID:7, locID:7) -> Node(reqID:8, locID:6) -> Node(reqID:9, locID:11) -> Node(reqID:10, locID:6)

----------
HubRoute from hub 1: Node(reqID:5, locID:22)
HubRoute from hub 2: Node(r

## Local Search 

In [227]:


def checkBetterState(instance, neighBour, costs, state, stateCost, dm, msg=None, i=None):
    neighBourCost = neighBour.computeCost(instance.VanDistanceCost, instance.VanDayCost, dm)
    if neighBourCost < stateCost:
        if neighBour.isFeasible(instance.VanCapacity, instance.VanMaxDistance, dm, verbose=False):
            neighBourCost = neighBour.computeCost(instance.VanDistanceCost, instance.VanDayCost, dm) #possible implement VanCost
            costs.append(neighBourCost)
            stateCost = neighBourCost
            print("New best: ", stateCost, i)
            print(state)
            print(neighBour)
            print(msg) if msg else None
            state = neighBour

    return neighBour, costs, state, stateCost


def localSearchDayHubRoutes(instance, dayHubRoutes: DayHubRoutes, distanceMatrix, maxTimeSeconds, maxIterations, nStart=5):
    maxTimeSeconds = maxTimeSeconds/nStart
    maxIterations = maxIterations/nStart
    bestState = None
    bestStateCost = math.inf
    for iteration in range(nStart):

        print("-"*10)

        startTime = time.time()
        costs = [dayHubRoutes.computeCost(instance.VanDistanceCost, instance.VanDayCost, distanceMatrix)]
        state = dayHubRoutes
        stateCost = costs[0]
        i = 0

        print("Starting localSearchDayHubRoutes at ", stateCost)
        while time.time() - startTime < maxTimeSeconds and i < maxIterations:

            neighBour = copy.deepcopy(state)
            neighBour.randomMergeRoutes()
            neighBour, costs, state, stateCost =checkBetterState(instance, neighBour, costs, state, stateCost, distanceMatrix,  msg="randomMergeRoutes",i=i)
            
            neighBour = copy.deepcopy(state)
            neighBour.randomNodeInsertion()
            neighBour, costs, state, stateCost =checkBetterState(instance, neighBour, costs, state, stateCost, distanceMatrix,  msg="randomMergeRoutes",i=i)

            neighBour = copy.deepcopy(state)
            neighBour.randomSectionInsertion()
            neighBour, costs, state, stateCost =checkBetterState(instance, neighBour, costs, state, stateCost, distanceMatrix,  msg="randomMergeRoutes",i=i)


            neighBour = copy.deepcopy(state)
            neighBour.shuffleRoute()
            neighBour, costs, state, stateCost =checkBetterState(instance, neighBour, costs, state, stateCost, distanceMatrix,  msg="randomMergeRoutes",i=i)

            i += 1

        print(i)

        if stateCost < bestStateCost:
            bestState = state
            bestStateCost = stateCost

    return bestState, bestStateCost

def localSearchHubRoutes(instance, hubRoutes: HubRoutes, maxTimeSeconds, maxIterations=math.inf, nStart=5):
    res = HubRoutes()
    dm = DistanceMatrix(instance)
    cost_begin = hubRoutes.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost, instance.deliverEarlyPenalty, dm)

    for day, dayHubRoutes in hubRoutes.hubRoutes.items(): #local search depot routes per day
        print("="*10, day, "="*10)
        if len(dayHubRoutes) > 0:
            dayres = localSearchDayHubRoutes(
                instance, dayHubRoutes, dm, maxTimeSeconds, maxIterations, nStart)
        else:
            dayres = [DayHubRoutes()]
        res.addDayHubRoutes(day, dayres[0])
    cost_end = res.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost, instance.deliverEarlyPenalty, dm)
    print(f"Finished searchHubRoutes resulting in cost decrease of {cost_begin}-{cost_end}={cost_begin-cost_end}")
    return res

##for part II

def localSearchDayEarlier(instance, hubRoutes: HubRoutes, distanceMatrix, maxTimeSeconds=5, maxIterations=math.inf, nStart=5):
    dm = distanceMatrix
    bestState = None
    bestStateCost = math.inf
    for iteration in range(nStart):
        print("-"*10)
        startTime = time.time()
        costs = [hubRoutes.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost, instance.deliverEarlyPenalty, dm)]
        state = hubRoutes
        stateCost = costs[0]

        i = 0
        print("Starting localSearchDayEarlier at ", stateCost)
        while time.time() - startTime < maxTimeSeconds and i < maxIterations:

            neighBour = copy.deepcopy(state)
            neighBour.randomMoveNodeDayEarly()

            neighBourCost = neighBour.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost, instance.deliverEarlyPenalty, dm)
            if neighBourCost < stateCost:
                if neighBour.isFeasible(instance.VanCapacity, instance.VanMaxDistance, dm, verbose=False):
                    neighBourCost = neighBour.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost,instance.deliverEarlyPenalty, dm) 
                    costs.append(neighBourCost)
                    stateCost = neighBourCost
                    print("New best: ", stateCost, i)
                    state = neighBour 
            i += 1

        if stateCost < bestStateCost:
            bestState = state
            bestStateCost = stateCost

        print(i)

    return bestState, bestStateCost


In [229]:
instance = loadInstance(11)
instance.CACHE_ID = 11
res = solveHub(instance)
dm = DistanceMatrix(instance)
test = parseToDayHubroutes(res)
print(test.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost, instance.deliverEarlyPenalty, dm))

35990.0


In [215]:
ls_result=test
print(ls_result.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost, instance.deliverEarlyPenalty, dm))

35990.0


In [231]:
#test localSearchHubRoutes
print(ls_result.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost, instance.deliverEarlyPenalty, dm))
ls_result = localSearchHubRoutes(instance, ls_result, maxTimeSeconds=5)
print(ls_result.computeCost(instance.VanDistanceCost,  instance.VanDayCost,instance.VanCost, instance.deliverEarlyPenalty, dm))

35990.0
========== 1 ==========
----------
Starting localSearchDayHubRoutes at  800.0
2103
----------
Starting localSearchDayHubRoutes at  800.0
1984
----------
Starting localSearchDayHubRoutes at  800.0
2147
----------
Starting localSearchDayHubRoutes at  800.0
1314
----------
Starting localSearchDayHubRoutes at  800.0
1048
========== 2 ==========
----------
Starting localSearchDayHubRoutes at  2410.0
New best:  1810.0 1
HubRoute from hub 2: Node(reqID:3, locID:23)
HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15)

HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15) -> Node(reqID:3, locID:23)

randomMergeRoutes
1930
----------
Starting localSearchDayHubRoutes at  2410.0
New best:  1810.0 0
HubRoute from hub 2: Node(reqID:3, locID:23)
HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15)

HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15) -> Node(reqID:3, locID:23)

randomMergeRoutes
1677
----------
Starting l

In [195]:
#test localSearchDayEarlier
print(ls_result.computeCost(instance.VanDistanceCost, instance.VanDayCost, instance.VanCost, instance.deliverEarlyPenalty, dm))
ls_result, _ = localSearchDayEarlier(instance, ls_result, dm, 10)
print(ls_result.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost,instance.deliverEarlyPenalty, dm))

35990.0
----------
Starting localSearchDayEarlier at  35990.0
HubRoute from hub 2: Node(reqID:45, locID:16)
Node(reqID:45, locID:16)
r2before HubRoute from hub 3: Node(reqID:42, locID:17) -> Node(reqID:43, locID:19)
r2after HubRoute from hub 3: Node(reqID:45, locID:16) -> Node(reqID:42, locID:17) -> Node(reqID:43, locID:19)
HubRoute from hub 2: Node(reqID:7, locID:13) -> Node(reqID:8, locID:7) -> Node(reqID:6, locID:22)
Node(reqID:7, locID:13)
r2before HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15)
r2after HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15) -> Node(reqID:7, locID:13)
HubRoute from hub 2: Node(reqID:18, locID:23) -> Node(reqID:17, locID:7) -> Node(reqID:19, locID:13)
Node(reqID:18, locID:23)
r2before HubRoute from hub 3: Node(reqID:15, locID:19) -> Node(reqID:16, locID:5)
r2after HubRoute from hub 3: Node(reqID:15, locID:19) -> Node(reqID:16, locID:5) -> Node(reqID:18, locID:23)
HubRoute from hub 2: Node(reqID:28, locID:10)
Nod

In [199]:
ls_result.deliverEarlyPenalty(5)

45

## Finishing using greedy02

In [223]:
def extractDays(hubRoutes, days: list) -> dict:
    res = {}
    for day, dayRoutes in hubRoutes.items():
        if day in days:
            for hubLocID in dayRoutes:
                newID = (day, hubLocID)
                res[newID] = dayRoutes[hubLocID]
    return res
    
def solve(instance: InstanceCO22, solveDaysEarly=False) -> dict:
    nDays = instance.Days
    nHubs = len(instance.Hubs)
    hubRoutes = solveHub(instance) 
    hubRoutes = parseToDayHubroutes(hubRoutes)

    if solveDaysEarly:
        hubRoutes,_ = localSearchDayEarlier(instance, hubRoutes, dm, 5)
    print("\n"*5,hubRoutes,"\n"*5)
    hubRoutes = localSearchHubRoutes(instance, hubRoutes, maxTimeSeconds=10, nStart=5)
    print("\n"*5,hubRoutes,"\n"*5)
    if solveDaysEarly:
        hubRoutes,_ = localSearchDayEarlier(instance, hubRoutes, dm, 5)
    print("\n"*5,hubRoutes,"\n"*5)
    hubRoutesDict = hubRoutes.toDict(instance)
   
    depotRoutes = {}
    dmin = min([_.daysFresh for _ in instance.Products])
     
    for i in range(0, math.ceil(nDays/dmin)):  
        periodBegin = dmin*i+1
        periodEnd = dmin*(i+1)+1
        print(i, periodBegin, periodEnd)
        period = list(range(periodBegin, periodEnd))
        periodRoutes = extractDays(hubRoutesDict, period)
        if len(periodRoutes)>0:                                                #depot routing
            res = solveDepotVRP(instance, periodRoutes)
            depotRoutes[periodBegin] = res
        else:
            depotRoutes[periodBegin] = {}

    return {'hubRoutes': hubRoutesDict, 'depotRoutes': depotRoutes}

In [222]:
def solutionToStr(instance: InstanceCO22, res: dict):
    resultString = "DATASET = CO2022_11 \n \n"

    for day in range(1, instance.Days+1):
        resultString += f"DAY = {day} \n"

        truckString = ""
        if day in res['depotRoutes'].keys():
            nTrucks = len(res['depotRoutes'][day])
            for routeID, truckRoute in res['depotRoutes'][day].items():
                truckString += f"{routeID} "
                for i, hubData in enumerate(truckRoute[1:-1]):
                    amountPerProduct = hubData['amounts']
                    truckString += f"H{hubData['locID'] - 1} {','.join([str(_) for _ in amountPerProduct])} "
                truckString += "\n"
        else:
            nTrucks = 0
            
        resultString += f"NUMBER_OF_TRUCKS = {nTrucks} \n"
        resultString += truckString

        nVans = 0
        i = 0
        vanString = ""
        for hubLocID in res['hubRoutes'][day].keys():
            for _, route in res['hubRoutes'][day][hubLocID]['routes'].items():
                i+=1
                reqIds = [_['reqID'] for _ in route['route'][1:-1] ]
                vanString += f"{i} H{hubLocID-1} {' '.join([str(_) for _ in reqIds])} \n"
            nVans += len(res['hubRoutes'][day][hubLocID]['routes'])
        resultString += f"NUMBER_OF_VANS = {nVans} \n"  
        resultString += vanString + "\n"
    return resultString
    

In [228]:
i = 11
solveDaysEarly = True
instance = loadInstance(i)
instance.CACHE_ID = i
res = solve(instance, solveDaysEarly)
solutionStr = solutionToStr(instance,res)
if solveDaysEarly:
    with open(f"./solutions/greedy01ls/solution{i}_DE.txt" ,'w') as file:
        file.write(solutionStr)
else:
    with open(f"./solutions/greedy01ls/solution{i}.txt" ,'w') as file:
        file.write(solutionStr)

INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 308 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 308 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 308.0
INFO:vrpy.master_solve_pulp:total cost = 308.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 194.0
INFO:vrpy.master_solve_pulp:total cost = 194.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 208 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 208 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 208.0
INFO:vrpy.master_solve_pulp:total cost = 208.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 302 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 302 and 1 vehic

----------
Starting localSearchDayEarlier at  35990.0
New best:  35815.0 5
New best:  35490.0 8
New best:  34745.0 11
New best:  34470.0 12
New best:  34275.0 14
New best:  33470.0 19
New best:  33385.0 26
New best:  32850.0 27
New best:  32285.0 30
2346
----------
Starting localSearchDayEarlier at  35990.0
New best:  35795.0 5
New best:  35520.0 6
New best:  34315.0 9
New best:  33510.0 14
New best:  33335.0 19
New best:  32800.0 53
New best:  32475.0 62
New best:  32350.0 79
New best:  32125.0 82
2768
----------
Starting localSearchDayEarlier at  35990.0
New best:  35805.0 3
New best:  35680.0 7
New best:  35485.0 18
New best:  34920.0 20
New best:  34835.0 27
New best:  34610.0 40
New best:  34285.0 43
New best:  34030.0 48
2147
----------
Starting localSearchDayEarlier at  35990.0
New best:  35065.0 0
New best:  34260.0 6
New best:  34065.0 12
New best:  33500.0 15
New best:  33225.0 17
New best:  32880.0 18
New best:  32605.0 29
New best:  32070.0 42
New best:  31845.0 252
3021
--

INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 481 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 481 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 481.0
INFO:vrpy.vrp:iteration 1, 481.0
INFO:vrpy.vrp:iteration 2, 481.0


2384





 ----------day 1----------
HubRoute from hub 2: Node(reqID:2, locID:6)
HubRoute from hub 3: Node(reqID:3, locID:23) -> Node(reqID:1, locID:20)

----------day 2----------
HubRoute from hub 3: Node(reqID:4, locID:8) -> Node(reqID:5, locID:15)

----------day 3----------
HubRoute from hub 2: Node(reqID:7, locID:13) -> Node(reqID:8, locID:7) -> Node(reqID:6, locID:22)

----------day 4----------
HubRoute from hub 3: Node(reqID:9, locID:21) -> Node(reqID:12, locID:11) -> Node(reqID:11, locID:6) -> Node(reqID:10, locID:22) -> Node(reqID:14, locID:23) -> Node(reqID:13, locID:12)

----------day 5----------
HubRoute from hub 3: Node(reqID:15, locID:19) -> Node(reqID:16, locID:5)

----------day 6----------
HubRoute from hub 2: Node(reqID:17, locID:7) -> Node(reqID:18, locID:23) -> Node(reqID:19, locID:13)

----------day 7----------

----------day 8----------
HubRoute from hub 3: Node(reqID:21, locID:15) -> Node(reqID:20, locID:21) -> Node(reqID:22, locID:9)

----------day 9----------
Hub

INFO:vrpy.master_solve_pulp:total cost = 481.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 770 and 2 vehicles
INFO:vrpy.vrp:Greedy solution found with value 770 and 2 vehicles
INFO:vrpy.vrp:iteration 0, 770.0
INFO:vrpy.master_solve_pulp:total cost = 770.0


1 12 23
dict_keys(['2.1', '3.1', 'Source', 'Sink'])


In [824]:
for i in range(20):
    print(i)
    instance = loadInstance(i)
    res = solve(instance)
    solutionStr = solutionToStr(instance,res)
    with open(f"./greedy01ls/solution{i}.txt" ,'w') as file:
        file.write(solutionStr)

0


AttributeError: 'InstanceCO22' object has no attribute 'Days'